Convert ROOT to h5 for WW analysis

In [1]:
import ROOT
from ROOT import gSystem, gInterpreter
import numpy as np
from tqdm import tqdm
import math
import os
import sys
import copy
import h5py

Welcome to JupyROOT 6.22/06


In [2]:
# parameters
MW = 80.379

In [3]:
folder_delphes='/home/dbfranzosi/MadGraph/2.9/mg5amcnlo/Delphes'

In [4]:
gInterpreter.AddIncludePath(folder_delphes)
gInterpreter.AddIncludePath(folder_delphes+"/external/")
gInterpreter.Declare('#include "'+folder_delphes+'/classes/DelphesClasses.h"')
gInterpreter.Declare('#include "'+folder_delphes+'/external/ExRootAnalysis/ExRootAnalysisLinkDef.h"')
gSystem.Load(folder_delphes+"/libDelphes.so")

0

In [5]:
def get_neutrino(pl_vec, MET_vec):
    
    pl = pl_vec.E()    
    pl_vec3 = pl_vec.Vect()    
    plT = pl_vec.Pt()
    plz = pl_vec.Pz()
    plT_vec3 = pl_vec.Vect()
    plT_vec3.SetZ(0.0)
    
    pvT = MET_vec.E()
    pvT_vec3 = MET_vec.Vect()
    pvT_vec3.SetZ(0.0)
    
    pvTplT = pvT_vec3.Dot(plT_vec3)
    
    a = plT**2
    b = -2*plz*(MW**2/2 + pvTplT)
    c = pl**2 * pvT**2 - (MW**2/2 + pvTplT)**2
    
    Delta = b**2 - 4*a*c
    
    if Delta > 0:
        pvzP = (-b + math.sqrt(Delta))/(2*a)
        pvzM = (-b - math.sqrt(Delta))/(2*a)
        
        pv_vec3P = pvT_vec3
        pv_vec3P.SetZ(pvzP)
        
        pv_vec3M = pvT_vec3
        pv_vec3M.SetZ(pvzM)
        
        if (pv_vec3P.Angle(pl_vec3) < pv_vec3M.Angle(pl_vec3)):
            pvz = pvzP
        else:
            pvz = pvzM        
        
    else:
        pvz = -b/(2*a)       
        
    pv_vec = MET_vec
    pv_vec.SetPz(pvz)
    pv_vec.SetE(math.sqrt(pvT**2 + pvz**2))
    
    return pv_vec  

In [6]:
def get_leptons(event):
    
    muons = list(filter(lambda Muons: np.abs(Muons.Eta) <= 5. and Muons.PT > 25., event.Muon))  
    electrons = list(filter(lambda Electrons: np.abs(Electrons.Eta) <= 5. and Electrons.PT > 25., event.Electron))        
    leptons = electrons + muons
   
    if leptons:
        leptons = sorted(leptons, key=lambda lepton: lepton.PT, reverse=True)
    
    MET = list(event.MissingET)
        
    pl = ROOT.TLorentzVector()
    MET_vec = ROOT.TLorentzVector() 
    if (leptons):
        pl.SetPtEtaPhiE(leptons[0].PT,leptons[0].Eta,leptons[0].Phi,leptons[0].P4().E())        
        MET_vec.SetPtEtaPhiE(MET[0].MET, 0.0, MET[0].Phi,MET[0].MET)
        # reconstruct neutrino
        pv = get_neutrino(pl, MET_vec) 
    else:
        pl.SetPtEtaPhiE(0.0,0.0,0.0,0.0)
        pv = ROOT.TLorentzVector()
        pv.SetPtEtaPhiE(0.0,0.0,0.0,0.0)
            
    return pl, pv

In [7]:
def get_jets(event, pt_cut:float=25., eta_cut:float=4.):
        
    jets = list(filter(lambda Jets: np.abs(Jets.Eta) <= eta_cut and Jets.PT > pt_cut, event.Jet))
    jets = sorted(jets, key=lambda Jets: Jets.PT, reverse=True)    
        
    # select the 2 jets (out of first for leading pt jets) with mjj~mw
    mjj = -1000.0
    iWj1, iWj2 = -1, -1
    cos_jet_W_ref = -10.
    for j1, jet1 in enumerate(jets):
        if j1 >= 4:
            break
            
        jet1_vec =  ROOT.TLorentzVector()
        jet1_vec.SetPtEtaPhiE(jet1.PT,jet1.Eta,jet1.Phi,jet1.P4().E())
                         
        for j2, jet2 in enumerate(jets[j1+1:], j1+1): 
            if j2 >= 4:
                break
                
            jet2_vec =  ROOT.TLorentzVector()
            jet2_vec.SetPtEtaPhiE(jet2.PT,jet2.Eta,jet2.Phi,jet2.P4().E())
            
            M = (jet1_vec + jet2_vec).M()
            if ( np.abs(M-MW) < np.abs(mjj-MW) ):
                mjj = M
                iWj1 = j1
                iWj2 = j2

    Wjet1_vec =  ROOT.TLorentzVector()
    Wjet2_vec =  ROOT.TLorentzVector()
    if (len(jets) >=2):        
        Wjet1_vec.SetPtEtaPhiE(jets[iWj1].PT,jets[iWj1].Eta,jets[iWj1].Phi,jets[iWj1].P4().E())        
        Wjet2_vec.SetPtEtaPhiE(jets[iWj2].PT,jets[iWj2].Eta,jets[iWj2].Phi,jets[iWj2].P4().E())        
    else:
        Wjet1_vec.SetPtEtaPhiE(0.,0.,0.,0.)        
        Wjet2_vec.SetPtEtaPhiE(0.,0.,0.,0.)
        
    return Wjet1_vec, Wjet2_vec 


In [8]:
def get_observables(event):
    
    pj1, pj2 = get_jets(event)
    pl, pv = get_leptons(event)
    
    mwlep = (pl + pv).M()
    mwhad = (pj1 + pj2).M()

    Wlep_vec = (pl + pv) 
    Whad_vec = (pj1 + pj2) 
    WW_vec = Wlep_vec + Whad_vec
        
    mww = WW_vec.M()

    # avoid modify pl and pv (now in the lab frame)
    pl_boosted = copy.deepcopy(pl) 
    pv_boosted = copy.deepcopy(pv) 

    # go to the WW rest frame if well defined
    if (pl.E() != 0.0 and pj1.E() != 0.0 and pj2.E() != 0.0):
        
        # get normal vectors of W+ - W- plane
        nWW = Wlep_vec.Vect().Cross(Whad_vec.Vect())

        WW_boost = WW_vec.BoostVector()

        Wlep_vec.Boost(-WW_boost) 
        pl_boosted.Boost(-WW_boost)
        pv_boosted.Boost(-WW_boost)
        
        # normal of and l-v plane
        nlv = pl_boosted.Vect().Cross(pv_boosted.Vect())
        phil_Wref = nWW.Angle(nlv)
    else:
        phil_Wref = -1000.0

    # go to the W rest frame
    if (pl.E() != 0.0):
        W_boost = Wlep_vec.BoostVector()    

        pl_boosted.Boost(-W_boost)
        pv_boosted.Boost(-W_boost)

        T3_lep_boost = pl_boosted.Vect()
        cosl_Wref = np.cos(T3_lep_boost.Angle(W_boost))        
    else:
        cosl_Wref = -1000.0
            
    return mwlep, mwhad, cosl_Wref, phil_Wref, mww

In [9]:
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt

def print_vec4(vec4, label='pmu= '):
    print(label, '{',vec4.Px(), ', ', vec4.Py(), ', ', vec4.Pz(), ', ', vec4.E(),'}')
def print_vec3(vec3, label='v= '):
    print(label, '{',vec3.X(), ', ', vec3.Y(), ', ', vec3.Z(),'}')

def visualize_vectors(vectors, size=1):
        colors=['r','r','b','b']
        soa = np.array(vectors)
        X, Y, Z, U, V, W = zip(*soa)
        fig = plt.figure()
        ax = fig.add_subplot(111, projection='3d')
        ax.quiver(X, Y, Z, U, V, W, color=colors)
        ax.set_xlim([-size, size])
        ax.set_ylim([-size, size])
        ax.set_zlim([-size, size])
        plt.show()

In [10]:
def get_truth(event):
    
    checks=False
    
    # Particles from hard scattering have status in [21,29]
    def IsHard(Status):
        return (Status == 1 or (Status >= 21 and Status <= 29))
    
    wps = list(filter(lambda Particles: Particles.PID == 24 and IsHard(Particles.Status), event.Particle))
    wms = list(filter(lambda Particles: Particles.PID == -24 and IsHard(Particles.Status), event.Particle))
    lms = list(filter(lambda Particles: (Particles.PID == 11 or Particles.PID == 13) 
                      and IsHard(Particles.Status), event.Particle))
    lps = list(filter(lambda Particles: (Particles.PID == -11 or Particles.PID == -13)
                     and IsHard(Particles.Status), event.Particle))
    vs = list(filter(lambda Particles: (Particles.PID == 12 or Particles.PID == 14)
                     and IsHard(Particles.Status), event.Particle))
    vbs = list(filter(lambda Particles: (Particles.PID == -12 or Particles.PID == -14)
                     and IsHard(Particles.Status), event.Particle))
    js = list(filter(lambda Particles: (np.abs(Particles.PID) < 6 or np.abs(Particles.PID) == 21) 
                     and IsHard(Particles.Status), event.Particle))    
    
    lsw=[]
    for ip, p in enumerate(lps):
        if (np.abs(event.Particle[p.M1].PID) == 24):
            lsw.append(p)
            
    for ip, p in enumerate(lms):
        if (np.abs(event.Particle[p.M1].PID) == 24):
            lsw.append(p)

    vsw=[]
    for ip, p in enumerate(vs):
        if (np.abs(event.Particle[p.M1].PID) == 24):
            vsw.append(p)
            
    for ip, p in enumerate(vbs):
        if (np.abs(event.Particle[p.M1].PID) == 24):
            vsw.append(p)
    
    jsw=[]
    jstag=[]
    jin=[]
    for ip, p in enumerate(js):
        if (np.abs(event.Particle[p.M1].PID) == 24):
            #print('jw status=', p.Status)
            jsw.append(p)
        elif (p.Status == 23): # ougoing status=23, ingoing =21
            #print('jtag status=', p.Status)
            jstag.append(p)
        else:
            jin.append(p)
    
    # look for W+W- in semi-leptonic channel
    if (len(lsw)== 1 and len(vsw)== 1 and len(jsw)== 2 and len(jstag)==0 and len(jin)==2):        
        pwm, pwp = ROOT.TLorentzVector(), ROOT.TLorentzVector()
        plw, pvw = ROOT.TLorentzVector(), ROOT.TLorentzVector()
        pjw1, pjw2 = ROOT.TLorentzVector(), ROOT.TLorentzVector()
        pjin1, pjin2 = ROOT.TLorentzVector(), ROOT.TLorentzVector()

        pwm.SetPtEtaPhiE(wms[0].PT,wms[0].Eta,wms[0].Phi,wms[0].P4().E())
        pwp.SetPtEtaPhiE(wps[0].PT,wps[0].Eta,wps[0].Phi,wps[0].P4().E())

        plw.SetPtEtaPhiE(lsw[0].PT,lsw[0].Eta,lsw[0].Phi,lsw[0].P4().E())
        pvw.SetPtEtaPhiE(vsw[0].PT,vsw[0].Eta,vsw[0].Phi,vsw[0].P4().E())
    
        pjw1.SetPtEtaPhiE(jsw[0].PT,jsw[0].Eta,jsw[0].Phi,jsw[0].P4().E())
        pjw2.SetPtEtaPhiE(jsw[1].PT,jsw[1].Eta,jsw[1].Phi,jsw[1].P4().E())  
        
        pjin1.SetPxPyPzE(jin[0].P4().Px(),jin[0].P4().Py(),jin[0].P4().Pz(),jin[0].P4().E())
        pjin2.SetPxPyPzE(jin[1].P4().Px(),jin[1].P4().Py(),jin[1].P4().Pz(),jin[1].P4().E())
        
        mwlep = (plw + pvw).M()
        mwhad = (pjw1 + pjw2).M()
        
        Wlep_vec = (plw + pvw) 
        Whad_vec = (pjw1 + pjw2)
        WW_vec = Wlep_vec + Whad_vec
        WpWm_vec = pwp + pwm
        
        mww = WW_vec.M()
        
        # get physical production plane
        nProdPlanePhy = Wlep_vec.Vect().Cross(Whad_vec.Vect()).Unit()        
        
                        
        # avoid modifying boosted momenta (now in the lab frame)
        pl_boosted = copy.deepcopy(plw) 
        pv_boosted = copy.deepcopy(pvw) 
        pwm_boosted = copy.deepcopy(Wlep_vec) 
        pwp_boosted = copy.deepcopy(Whad_vec) 
        pjin1_boosted = copy.deepcopy(pjin1) 
        
        # go to the WW rest frame
        WW_boost = WW_vec.BoostVector()
        
        pwm_boosted.Boost(-WW_boost) 
        pl_boosted.Boost(-WW_boost)
        pv_boosted.Boost(-WW_boost)
        
        # get production plane
        nj1 = pjin1_boosted.Vect().Unit()
        nWm = pwm_boosted.Vect().Unit()

        nProdPlane = nWm.Cross(nj1).Unit()       
        
        # go to the W rest frame
        W_boost = pwm_boosted.BoostVector()    
    
        pl_boosted.Boost(-W_boost)
        pv_boosted.Boost(-W_boost)
        
        # get normal vector of l-W plane
        nl = pl_boosted.Vect().Unit()
        nv = pv_boosted.Vect().Unit()

        nDecayPlane = nl.Cross(nWm).Unit()
        phil_Wref = nProdPlane.Angle(nDecayPlane)       
        
        T3_lep_boost = pl_boosted.Vect()
        cosl_Wref = np.cos(T3_lep_boost.Angle(W_boost))

        ###################
        #Checks
        ###############
        if (checks):        
            print_vec3(nj1, 'nj1=')
            print_vec3(nWm, 'nWm=')
            print_vec3(nl, 'nl =')
            print_vec3(nv, 'nv =')
            vectors = [
                [0, 0, 0, nj1.Px(), nj1.Py(), nj1.Pz()], 
                [0, 0, 0, nWm.Px(), nWm.Py(), nWm.Pz()], 
                #[nWm.Px(), nWm.Py(), nWm.Pz(), nl.Px(), nl.Py(), nl.Pz()], 
                #[nWm.Px(), nWm.Py(), nWm.Pz(), nv.Px(), nv.Py(), nv.Pz()]  
                [0, 0, 0, nl.Px(), nl.Py(), nl.Pz()], 
                [0, 0, 0, nv.Px(), nv.Py(), nv.Pz()]  
                ]
            visualize_vectors(vectors)

            print_vec3(nProdPlane, 'nProdPlane=')
            print_vec3(nDecayPlane, 'nDecayPlane=')        
            print('phi=', phil_Wref)
            print('PhysXj=', nProdPlanePhy.Angle(nProdPlane))


            nvectors = [
            [0, 0, 0, nProdPlane.Px(), nProdPlane.Py(), nProdPlane.Pz()], 
            [0, 0, 0, nDecayPlane.Px(), nDecayPlane.Py(), nDecayPlane.Pz()]
            ]
            visualize_vectors(nvectors)

            '''
            print('4vec:')
            print_vec4(pwm, label='pWm=')
            print_vec4(pwp, label='pWp=')

            print_vec4(Wlep_vec, label='pWlep=')
            print_vec4(Whad_vec, label='pWhad=')

            print_vec4(WW_vec, label='pWW=')
            print_vec4(pjin1, label='pjin1=')        
            print_vec4(pjin2, label='pjin2=')  

            # get normal vectors of (W-,j1) plane
            nWW = Wlep_vec.Vect().Cross(Whad_vec.Vect())
            nWj1 = pwm.Vect().Cross(pjin1.Vect())
            nWj2 = pwm.Vect().Cross(pjin2.Vect())
            nWpWm = pwm.Vect().Cross(pwp.Vect())

            print('normal')
            #print_vec3(nWpWm, 'nWpWm=')
            #print_vec3(nWW, 'nWW=')
            print_vec3(nWj1, 'nWj1=')
            print_vec3(nWj2, 'nWj2=')

            #print('angle=', nWj1.Angle(nWW), ', ', nWpWm.Angle(nWW))
            #print('angWj=', nWpWm.Angle(nWj1), ', ', nWpWm.Angle(nWj2))
            # Wj1, Wj2 and WW define the same plane 

            '''
            ########### End checks
        
    else:
        print('Counts')
        print('jsw=',len(jsw))
        print('lsw=', len(lsw))
        print('vsw=',len(vsw))
        print('jstag=',len(jstag))
        print('jsin=',len(jin))
        return 0
        
    return mwlep, mwhad, cosl_Wref, phil_Wref, mww


In [11]:
def gen_h5(folder_gen, run_name, max_events):

    chain1 = ROOT.TChain("Delphes")
    #file_name = '/home/dbfranzosi/MadGraph/2.9/mg5amcnlo/'+folder_gen+'/Events/'+run_name+'/tag_2_delphes_events.root'
    file_name = '/home/dbfranzosi/remoteLink/MG5_aMC_v2_8_2/Generations/'+folder_gen+'/Events/'+run_name+'/tag_1_delphes_events.root'
    print('Reading ', file_name)
    chain1.Add(file_name)
    print('Number of entries=', chain1.GetEntries())
    
    detector_info = []
    truth_info = []
    weights = []

    detector_info_names = ['mwlep_det', 'mwhad_det', 'cosl_Wref_det', 'phil_Wref_det', 'mww_det']
    truth_info_names = ['mwlep_truth', 'mwhad_truth', 'cosl_Wref_truth', 'phil_Wref_truth', 'mww_truth']

    for count, event in enumerate(tqdm(chain1, total=chain1.GetEntries())):

        if count == max_events:
            break
            
        truth = get_truth(event)
        det = get_observables(event)
        
        event_weight = [eevent.Weight for eevent in event.Event]
        xs_weight = event_weight[0] if len(event_weight) == 1 else 0

        weights.append(xs_weight)
        detector_info.append(det)
        truth_info.append(truth)

    # Create array of events from list
    detector_info = np.array(detector_info)    
    truth_info = np.array(truth_info)
    
    output_name = './data/'+folder_gen+'.h5'
    print('Writing ', output_name)
    with h5py.File(output_name, 'w') as h5f:
        h5f.create_dataset('weights'   , data = weights, compression='gzip')
        h5f.create_dataset('detector_info'  , data = detector_info, compression='gzip')
        h5f.create_dataset('truth_info', data = truth_info, compression='gzip')

        h5f.create_dataset('detector_info_names'  , data = detector_info_names, compression='gzip')
        h5f.create_dataset('truth_info_names', data = truth_info_names, compression='gzip')


In [12]:
#gen_h5('PROC_sm_pp-wwT','run_02_decayed_1',-1)
#gen_h5('PROC_bsm_pp-wwT','run_01_decayed_1',-1)

#gen_h5('PROC_sm_pp-ww0','run_02_decayed_1',-1)
#gen_h5('PROC_bsm_pp-ww0','run_01_decayed_1',-1)

#gen_h5('PROC_sm_pp-ww','run_02_decayed_1',-1)
gen_h5('PROC_bsm_pp-ww','run_02_decayed_1',-1)

#from local folder
#gen_h5('PROC_sm_pp-wwT','run_01_decayed_1',-1)
#gen_h5('PROC_sm_pp-ww0','run_01_decayed_1',-1)
#gen_h5('PROC_bsm_pp-ww0','run_01_decayed_1',-1)
#gen_h5('PROC_bsm_pp-wwT','run_01_decayed_1',-1)



Reading  /home/dbfranzosi/remoteLink/MG5_aMC_v2_8_2/Generations/PROC_bsm_pp-ww/Events/run_02_decayed_1/tag_1_delphes_events.root
Number of entries=

  0%|          | 0/46229 [00:00<?, ?it/s]

 46229


100%|██████████| 46229/46229 [1:29:24<00:00,  8.62it/s]   


Writing  ./data/PROC_bsm_pp-ww.h5


Warning in <TStreamerInfo::BuildCheck>: 
   The StreamerInfo of class GenParticle read from file /home/dbfranzosi/remoteLink/MG5_aMC_v2_8_2/Generations/PROC_bsm_pp-ww/Events/run_02_decayed_1/tag_1_delphes_events.root
   has the same version (=2) as the active class but a different checksum.
   You should update the version to ClassDef(GenParticle,3).
   Do not try to write objects with the current class definition,
   the files will not be readable.

Warning in <TStreamerInfo::CompareContent>: The following data member of
the in-memory layout version 2 of class 'GenParticle' is missing from 
the on-file layout version 2:
   float CtgTheta; //
Warning in <TStreamerInfo::CompareContent>: The following data member of
the in-memory layout version 2 of class 'GenParticle' is missing from 
the on-file layout version 2:
   float D0; //
Warning in <TStreamerInfo::CompareContent>: The following data member of
the in-memory layout version 2 of class 'GenParticle' is missing from 
the on-file lay